In [6]:
import pandas as pd
import polars as pl
import datetime as dt
pd.set_option("display.max_rows", 25_000)
pd.set_option("display.max_columns", 500)
pl.Config.set_tbl_cols(500)
pl.Config.set_tbl_rows(10_000)
import numpy as np

In [7]:
import sys

sys.path.append("..")
from tooling.enums import AssetClass, Index, Spot, StrikeSpread
from tooling.fetch import fetch_option_data, fetch_spot_data
from tooling.filter import find_atm, option_tool

from fetching_from_local_db.enums import AssetClass, Index, StrikeSpread
from fetching_from_local_db.fetch_from_db import _fetch_batch, fetch_data, fetch_spot_data

In [8]:
tb = pd.read_csv('Budget_straddle_11_15.csv')
# tb = tb.drop(columns=['Unnamed: 0'])

In [9]:
tb.tail(500)

Day      Time  Strike      Expiry  DTE Option Type  Entry Price  \
0   2019-07-05  11:05:00   11950  2019-07-11    6          CE       101.85   
1   2019-07-05  11:05:00   11950  2019-07-11    6          PE        87.80   
2   2020-02-01  11:05:00   11950  2020-02-06    5          CE       160.10   
3   2020-02-01  11:05:00   11950  2020-02-06    5          PE       132.85   
4   2021-02-01  11:05:00   13750  2021-02-04    3          CE       208.30   
5   2021-02-01  11:05:00   13750  2021-02-04    3          PE       198.40   
6   2022-02-01  11:05:00   17550  2022-02-03    2          CE       245.05   
7   2022-02-01  11:05:00   17550  2022-02-03    2          PE       210.05   
8   2023-02-01  11:05:00   17800  2023-02-02    1          CE       156.30   
9   2023-02-01  11:05:00   17800  2023-02-02    1          PE        95.95   
10  2024-02-01  11:05:00   21800  2024-02-01    0          CE        98.05   
11  2024-02-01  11:05:00   21800  2024-02-01    0          PE        98.20   
12  2024-07-23  11:05:00   24550  2024-07-25    2          CE       201.60   
13  2024-07-23  11:05:00   24550  2024-07-25    2          PE       232.35   

    Initial SL  Exit Price            Exit Time  Max Price After Entry  \
0      112.035      20.000  2019-07-05 15:30:00                 104.60   
1       96.580      96.580  2019-07-05 11:25:00                 170.40   
2      176.110      16.750  2020-02-01 15:29:00                 174.30   
3      146.135     146.135  2020-02-01 11:26:00                 343.15   
4      229.130     229.130  2021-02-01 11:20:00                 615.15   
5      218.240      12.000  2021-02-01 15:29:00                 198.75   
6      269.555     160.000  2022-02-01 15:30:00                 258.80   
7      231.055     231.055  2022-02-01 11:27:00                 379.75   
8      171.930     171.930  2023-02-01 12:32:00                 215.90   
9      105.545     105.545  2023-02-01 11:11:00                 420.00   
10     107.855       0.050  2024-02-01 15:30:00                  97.85   
11     108.020     108.020  2024-02-01 11:06:00                 207.00   
12     221.760      71.100  2024-07-23 15:30:00                 220.00   
13     255.585     255.585  2024-07-23 11:17:00                 519.50   

    Min Price After Entry   Points          Qty            Pnl  Slippage  \
0                   18.50   81.850  1171.548117   95891.213389    2.4370   
1                   77.00   -8.780  1171.548117  -10286.192469    3.6876   
2                   14.30  143.350  1171.548117  167941.422594    3.5370   
3                  119.35  -13.285  1171.548117  -15564.016736    5.5797   
4                  196.50  -20.830   960.153625  -20000.000000    8.7486   
5                   12.00  186.400  1008.064516  187903.225806    4.2080   
6                   57.15   85.050   797.720798   67846.153846    8.1010   
7                  106.25  -21.005   797.720798  -16756.125356    8.8221   
8                   11.80  -15.630   786.516854  -12293.258427    6.5646   
9                   26.30   -9.595   786.516854   -7546.629213    4.0299   
10                   0.05   98.000   642.201835   62935.779817    1.9620   
11                  71.00   -9.820   642.201835   -6306.422018    4.1244   
12                  37.90  130.500   570.264766   74419.551935    5.4540   
13                 116.40  -23.235   570.264766  -13250.101833    9.7587   

        Final PnL      Margin       ROI%  
0    93036.150628  200.000000   9.303615  
1   -14606.393305  200.000000  -1.460639  
2   163797.656904  200.000000  16.379766  
3   -22100.903766  200.000000  -2.210090  
4   -28400.000000  188.601605  -2.840000  
5   183661.290323  198.012673  18.366129  
6    61383.817664  200.000000   6.138382  
7   -23793.698006  200.000000  -2.379370  
8   -17456.426966  200.000000  -1.745643  
9   -10716.213483  200.000000  -1.071621  
10   61675.779817  200.000000   6.167578  
11   -8955.119266  200.000000  -0.895512  
12   71309.327902  200.000000

In [10]:
tb['ROI%'].sum()

49.002012384136044

In [11]:
# def round_to_nearest_50(value):
#     return int(50 * round(value / 50))

# def get_hedge_pct(margin):
#     if 100 < margin <= 150:
#         return 5
#     elif 150 < margin <= 200:
#         return 4
#     elif 200 < margin < 300:
#         return 3
#     else:
#         return 0  # Default value if margin doesn't fit any range

# async def add_hedges(df):
#     # df.drop(columns=['ROI%', 'Trade Year'], inplace=True)
#     # hedge_pct = 2.75
#     index_name = "NIFTY"
#     index_str_for_opt = "nifty"

#     df["Hedge Strike"] = df.apply(
#         lambda row: (
#             int(round_to_nearest_50(row["strike"] * (1 + (get_hedge_pct(row["Margin"]) / 100))))
#             if row["type"] == "C" and row["Margin"] > 100
#             else int(round_to_nearest_50(row["strike"] * (1 - (get_hedge_pct(row["Margin"]) / 100))))
#             if row["type"] == "P" and row["Margin"] > 100
#             else 0  # Default value if neither condition matches
#         ),
#         axis=1,
#     )

#     # df["Hedge Contract"] = df.apply(
#     #     lambda row: get_option_contract_name2(
#     #         index_name, row["Hedge Strike"], row["Expiry"], row["Option Type"]
#     #     ),
#     #     axis=1,
#     # )

#     df["Hedge Entry Price"] = np.nan
#     df["Hedge Exit Price"] = np.nan

#     # print(df['Hedge Strike'].to_string())

#     for i in range(0, len(df)):
#         print(df.iloc[i]['date'])
#         if df.iloc[i]['Hedge Strike']:
#             # print(df.iloc[i]["Week"])
#             entry_date = df.iloc[i]['date']
#             entry_time = df.iloc[i]['Entry Time']
#             exit_date = df.iloc[i]['Exit date']
#             exit_time = df.iloc[i]['Exit Time']
#             hedge_strike = int(df.iloc[i]["Hedge Strike"])
#             hedge_expiry = df.iloc[i]["expiry"]
#             hedge_opt_type = df.iloc[i]["type"]
#             # hedge_entry_datetime = dt.datetime.combine(entry_date, entry_time)
#             # hedge_exit_datetime = dt.datetime.combine(exit_date, exit_time)
    
#             hedge_df = await fetch_data(
#                 index=index_str_for_opt,
#                 start_date=dt.datetime.strptime(entry_date, "%Y-%m-%d").date(),
#                 end_date=dt.datetime.strptime(exit_date, "%Y-%m-%d").date(),
#                 start_time=dt.datetime.strptime(entry_time, "%H:%M:%S").time(),
#                 end_time=dt.datetime.strptime(exit_time, "%H:%M:%S").time(),
#                 expiry=dt.datetime.strptime(hedge_expiry, "%Y-%m-%d"),
#                 strike=hedge_strike,
#                 asset_class=hedge_opt_type,
#             )
#             if not isinstance(hedge_df, str) and hedge_df is not None:
#                 hedge_df = hedge_df.to_pandas()
#             else:
#                 print(hedge_df)
#                 df.loc[i, "Hedge Entry Price"] = 0
#                 df.loc[i, "Hedge Exit Price"] = 0
#                 continue
#             # print(hedge_df)
    
#             hedge_entry_price = hedge_df.iloc[0]["c"]
#             hedge_exit_price = hedge_df.iloc[-1]["c"]
    
#             print(hedge_entry_price, hedge_exit_price)
    
#             df.loc[i, "Hedge Entry Price"] = hedge_entry_price
#             df.loc[i, "Hedge Exit Price"] = hedge_exit_price
    
#     return df

In [14]:
def round_to_nearest_50(value):
    return int(50 * round(value / 50))

def get_hedge_pct(margin):
    if 100 < margin <= 150:
        return 4
    elif 150 < margin <= 200:
        return 3
    elif 200 < margin < 300:
        return 2
    else:
        return 0  # Default value if margin doesn't fit any range

async def add_hedges(df):
    # df.drop(columns=['ROI%', 'Trade Year'], inplace=True)
    # hedge_pct = 2.75
    index_name = "NIFTY"
    index_str_for_opt = "nifty"

    df["Hedge Strike"] = df.apply(
        lambda row: (
            int(round_to_nearest_50(row["Strike"] * (1 + (get_hedge_pct(row["Margin"]) / 100))))
            if row["Option Type"] == "CE" and row["Margin"] > 100
            else int(round_to_nearest_50(row["Strike"] * (1 - (get_hedge_pct(row["Margin"]) / 100))))
            if row["Option Type"] == "PE" and row["Margin"] > 100
            else 0  # Default value if neither condition matches
        ),
        axis=1,
    )

    # df["Hedge Contract"] = df.apply(
    #     lambda row: get_option_contract_name2(
    #         index_name, row["Hedge Strike"], row["Expiry"], row["Option Type"]
    #     ),
    #     axis=1,
    # )

    df["Hedge Entry Price"] = np.nan
    df["Hedge Exit Price"] = np.nan

    # print(df['Hedge Strike'].to_string())

    df['Entry Time'] = df['Time']

    for i in range(0, len(df)):
        print(df.iloc[i]['Day'])
        if df.iloc[i]['Hedge Strike']:
            # print(df.iloc[i]["Week"])
            entry_date = df.iloc[i]['Day']
            entry_time = df.iloc[i]['Entry Time']
            exit_date = df.iloc[i]['Day']
            exit_time = pd.to_datetime(df.iloc[i]['Exit Time']).time()
            hedge_strike = int(df.iloc[i]["Hedge Strike"])
            hedge_expiry = df.iloc[i]["Expiry"]
            hedge_opt_type = df.iloc[i]["Option Type"]
            # hedge_entry_datetime = dt.datetime.combine(entry_date, entry_time)
            # hedge_exit_datetime = dt.datetime.combine(exit_date, exit_time)
    
            hedge_df = await fetch_data(
                index=index_str_for_opt,
                start_date=dt.datetime.strptime(entry_date, "%Y-%m-%d").date(),
                end_date=dt.datetime.strptime(exit_date, "%Y-%m-%d").date(),
                start_time=pd.to_datetime(entry_time).time(),
                end_time=exit_time,
                expiry=dt.datetime.strptime(hedge_expiry, "%Y-%m-%d"),
                strike=hedge_strike,
                asset_class=hedge_opt_type[:1],
            )
            if not isinstance(hedge_df, str) and hedge_df is not None:
                hedge_df = hedge_df.to_pandas()
            else:
                print(hedge_df)
                df.loc[i, "Hedge Entry Price"] = 0
                df.loc[i, "Hedge Exit Price"] = 0
                continue
            # print(hedge_df)
    
            hedge_entry_price = hedge_df.iloc[0]["c"]
            hedge_exit_price = hedge_df.iloc[-1]["c"]
    
            print(hedge_entry_price, hedge_exit_price)
    
            df.loc[i, "Hedge Entry Price"] = hedge_entry_price
            df.loc[i, "Hedge Exit Price"] = hedge_exit_price
    
    return df

In [15]:
tb_with_hedge = await add_hedges(tb)
# tb_with_hedge.tail()

2019-07-05
7.2 1.55
2019-07-05
10.5 11.65
2020-02-01
44.7 4.35
2020-02-01
33.6 33.8
2021-02-01
55.05 65.45
2021-02-01
71.7 5.55
2022-02-01
59.95 14.0
2022-02-01
49.9 57.15
2023-02-01
9.75 6.2
2023-02-01
9.9 10.3
2024-02-01
9.65 0.05
2024-02-01
6.35 7.8
2024-07-23
32.35 3.0
2024-07-23
38.5 43.75


In [16]:
tb_with_hedge['Hedge Points'] = tb_with_hedge['Hedge Exit Price'] - tb_with_hedge['Hedge Entry Price']
tb_with_hedge['Hedge PnL'] = tb_with_hedge['Hedge Points'] * tb_with_hedge['Qty']
tb_with_hedge['Hedge ROI%'] = tb_with_hedge.apply(
    lambda row: (row['Hedge PnL'] * 100 / 1000000) if not pd.isna(row['Hedge Points']) else 0,
    axis=1
)
tb_with_hedge['Total ROI%'] = tb_with_hedge['ROI%'] + tb_with_hedge['Hedge ROI%']

In [17]:
tb_with_hedge['ROI%'].sum(), tb_with_hedge['Total ROI%'].sum()

(49.002012384136044, 32.868598159288595)

In [25]:
tb_with_hedge.tail(8)

Day      Time  Strike      Expiry  DTE Option Type  Entry Price  \
6  2022-02-01  11:05:00   17550  2022-02-03    2          CE       245.05   
7  2022-02-01  11:05:00   17550  2022-02-03    2          PE       210.05   
8  2023-02-01  11:05:00   17800  2023-02-02    1          CE       156.30   
9  2023-02-01  11:05:00   17800  2023-02-02    1          PE        95.95   
10 2024-02-01  11:05:00   21800  2024-02-01    0          CE        98.05   
11 2024-02-01  11:05:00   21800  2024-02-01    0          PE        98.20   
12 2024-07-23  11:05:00   24550  2024-07-25    2          CE       201.60   
13 2024-07-23  11:05:00   24550  2024-07-25    2          PE       232.35   

    Initial SL  Exit Price            Exit Time  Max Price After Entry  \
6      269.555     160.000  2022-02-01 15:30:00                 258.80   
7      231.055     231.055  2022-02-01 11:27:00                 379.75   
8      171.930     171.930  2023-02-01 12:32:00                 215.90   
9      105.545     105.545  2023-02-01 11:11:00                 420.00   
10     107.855       0.050  2024-02-01 15:30:00                  97.85   
11     108.020     108.020  2024-02-01 11:06:00                 207.00   
12     221.760      71.100  2024-07-23 15:30:00                 220.00   
13     255.585     255.585  2024-07-23 11:17:00                 519.50   

    Min Price After Entry   Points         Qty           Pnl  Slippage  \
6                   57.15   85.050  797.720798  67846.153846    8.1010   
7                  106.25  -21.005  797.720798 -16756.125356    8.8221   
8                   11.80  -15.630  786.516854 -12293.258427    6.5646   
9                   26.30   -9.595  786.516854  -7546.629213    4.0299   
10                   0.05   98.000  642.201835  62935.779817    1.9620   
11                  71.00   -9.820  642.201835  -6306.422018    4.1244   
12                  37.90  130.500  570.264766  74419.551935    5.4540   
13                 116.40  -23.235  570.264766 -13250.101833    9.7587   

       Final PnL  Margin      ROI%  Hedge Strike  Hedge Entry Price  \
6   61383.817664   200.0  6.138382         18100              59.95   
7  -23793.698006   200.0 -2.379370         17000              49.90   
8  -17456.426966   200.0 -1.745643         18350               9.75   
9  -10716.213483   200.0 -1.071621         17250               9.90   
10  61675.779817   200.0  6.167578         22450               9.65   
11  -8955.119266   200.0 -0.895512         21150               6.35   
12  71309.327902   200.0  7.130933         25300              32.35   
13 -18815.144603   200.0 -1.881514         23800              38.50   

    Hedge Exit Price Entry Time  Hedge Points     Hedge PnL  Hedge ROI%  \
6              14.00   11:05:00        -45.95 -36655.270655   -3.665527   
7              57.15   11:05:00          7.25   5783.475783    0.578348   
8               6.20   11:05:00         -3.55  -2792.134831   -0.279213   
9              10.30   11:05:00          0.40    314.606742    0.031461   
10              0.05   11:05:00         -9.60  -6165.137615   -0.616514   
11              7.80   11:05:00          1.45    931.192661    0.093119   
12              3.00   11:05:00        -29.35 -16737.270876   -1.673727   
13             43.75   11:05:00          5.25   2993.890020    0.299389   

    Total ROI%  Trade Year  
6     2.472855        2022  
7    -1.801022        2022  
8    -2.024856        2023  
9    -1.040161        2023  
10    5.551064        2024  
11   -0.802393        2024  
12    5.457206        2024  
13   -1.582125        2024

In [19]:
def generate_stats(tb_expiry, ema_window):
    stats_df8 = pd.DataFrame(
        index=range(2019, 2025),
        columns=[
            "Total ROI",
            "Total Trades",
            "Win Rate",
            "Avg Profit% per Trade",
            "Avg Loss% per Trade",
            "Max Drawdown",
            "ROI/DD Ratio",
            "Variation",
        ],
    )
    combined_df_sorted = tb_expiry
    # combined_df_sorted = tb_expiry_ce
    # combined_df_sorted = tb_expiry_pe

    # Iterate over each year
    for year in range(2019, 2025):
        # Filter trades for the current year
        year_trades = combined_df_sorted[(combined_df_sorted["Trade Year"] == year)]

        # Calculate total ROI
        total_roi = year_trades["Total ROI%"].sum()

        # Calculate total number of trades
        total_trades = len(year_trades)

        # Calculate win rate
        win_rate = (year_trades["Total ROI%"] > 0).mean() * 100

        # Calculate average profit per trade
        avg_profit = year_trades[year_trades["Total ROI%"] > 0]["Total ROI%"].mean()

        # Calculate average loss per trade
        avg_loss = year_trades[year_trades["Total ROI%"] < 0]["Total ROI%"].mean()

        # Calculate maximum drawdown
        max_drawdown = (
            year_trades["Total ROI%"].cumsum() - year_trades["Total ROI%"].cumsum().cummax()
        ).min()

        # Calculate ROI/DD ratio
        roi_dd_ratio = total_roi / abs(max_drawdown)

        variation = f"{ema_window}"

        # Store the statistics in the DataFrame
        stats_df8.loc[year] = [
            total_roi,
            total_trades,
            win_rate,
            avg_profit,
            avg_loss,
            max_drawdown,
            roi_dd_ratio,
            variation,
        ]

    # Calculate overall statistics
    overall_total_roi = stats_df8["Total ROI"].sum()
    overall_total_trades = stats_df8["Total Trades"].sum()
    overall_win_rate = (combined_df_sorted["Total ROI%"] > 0).mean() * 100
    overall_avg_profit = combined_df_sorted[combined_df_sorted["Total ROI%"] > 0][
        "Total ROI%"
    ].mean()
    overall_avg_loss = combined_df_sorted[combined_df_sorted["Total ROI%"] < 0]["Total ROI%"].mean()
    overall_max_drawdown = (
        combined_df_sorted["Total ROI%"].cumsum()
        - combined_df_sorted["Total ROI%"].cumsum().cummax()
    ).min()
    overall_roi_dd_ratio = overall_total_roi / abs(overall_max_drawdown)
    overall_variation = variation

    # Store the overall statistics in the DataFrame
    stats_df8.loc["Overall"] = [
        overall_total_roi,
        overall_total_trades,
        overall_win_rate,
        overall_avg_profit,
        overall_avg_loss,
        overall_max_drawdown,
        overall_roi_dd_ratio,
        overall_variation,
    ]
    return {overall_roi_dd_ratio: stats_df8}

In [21]:
tradebook = tb
tradebook["Day"] = pd.to_datetime(tradebook["Day"])
tradebook["Trade Year"] = tradebook["Day"].dt.year

In [26]:
stats = generate_stats(tradebook, 'Lobster Budget W Hedges')
for x, y in stats.items():
    z = pd.DataFrame(y)
    break

z

/tmp/ipykernel_49742/1485017518.py:45: RuntimeWarning: divide by zero encountered in scalar divide
  roi_dd_ratio = total_roi / abs(max_drawdown)


Total ROI Total Trades   Win Rate Avg Profit% per Trade  \
2019      7.315779            2       50.0               8.64169   
2020       9.46591            2       50.0             11.652569   
2021      9.856342            2       50.0             11.697782   
2022      0.671832            2       50.0              2.472855   
2023     -3.065017            2        0.0                   NaN   
2024      8.623752            4       50.0              5.504135   
Overall  32.868598           14  42.857143              7.578861   

        Avg Loss% per Trade Max Drawdown ROI/DD Ratio               Variation  
2019              -1.325911    -1.325911     5.517548  LobsterBudget W Hedges  
2020              -2.186659    -2.186659     4.328936  LobsterBudget W Hedges  
2021               -1.84144          0.0          inf  LobsterBudget W Hedges  
2022              -1.801022    -1.801022     0.373028  LobsterBudget W Hedges  
2023              -1.532508    -1.040161    -2.946676  LobsterBudget W Hedges  
2024              -1.192259    -1.582125     5.450738  LobsterBudget W Hedges  
Overall           -1.575571    -4.866039     6.754693  LobsterBudget W Hedges

In [61]:
# import pandas as pd

# df = pd.DataFrame(tb_with_hedge)

# cols = df.columns.tolist()

# # Move 'Cumulative ROI%', 'Max Cumulative ROI%' and 'DD' to the last
# desired_cols = ['Cumulative ROI%', 'Max Cumulative ROI%', 'DD']
# cols = [col for col in cols if col not in desired_cols] + desired_cols
# # Reassign the columns to the DataFrame
# df = df[cols]

# df


In [76]:
tb = tb_with_hedge
tb['Cumulative ROI%'] = tb['Total ROI%'].cumsum()
tb['Max Cumulative ROI%'] = tb['Cumulative ROI%'].cummax()  # Maximum value so far
tb['DD'] = tb['Cumulative ROI%'] - tb['Max Cumulative ROI%']  # Drawdown
tb

Day  Strike      Expiry  DTE Option Type  Entry Price  \
0     2019-01-01   11000  2019-01-03    2          CE          NaN   
1     2019-01-01   10750  2019-01-03    2          PE          NaN   
2     2019-01-02   11000  2019-01-03    1          CE          NaN   
3     2019-01-02   10750  2019-01-03    1          PE          NaN   
4     2019-01-03   10900  2019-01-03    0          CE          NaN   
5     2019-01-03   10700  2019-01-03    0          PE          NaN   
6     2019-01-04   10800  2019-01-10    6          CE          NaN   
7     2019-01-04   10600  2019-01-10    6          PE          NaN   
8     2019-01-07   10900  2019-01-10    3          CE          NaN   
9     2019-01-07   10700  2019-01-10    3          PE          NaN   
10    2019-01-08   10900  2019-01-10    2          CE          NaN   
11    2019-01-08   10700  2019-01-10    2          PE          NaN   
12    2019-01-09   10950  2019-01-10    1          CE          NaN   
13    2019-01-09   10750  2019-01-10    1          PE          NaN   
14    2019-01-10   10950  2019-01-10    0          CE          NaN   
15    2019-01-10   10750  2019-01-10    0          PE          NaN   
16    2019-01-11   10950  2019-01-17    6          CE          NaN   
17    2019-01-11   10750  2019-01-17    6          PE          NaN   
18    2019-01-14   10900  2019-01-17    3          CE          NaN   
19    2019-01-14   10700  2019-01-17    3          PE          NaN   
20    2019-01-15   10900  2019-01-17    2          CE          NaN   
21    2019-01-15   10650  2019-01-17    2          PE          NaN   
22    2019-01-16   11000  2019-01-17    1          CE          NaN   
23    2019-01-16   10800  2019-01-17    1          PE          NaN   
24    2019-01-17   11050  2019-01-17    0          CE          NaN   
25    2019-01-17   10800  2019-01-17    0          PE          NaN   
26    2019-01-18   11000  2019-01-24    6          CE          NaN   
27    2019-01-18   10800  2019-01-24    6          PE          NaN   
28    2019-01-21   11050  2019-01-24    3          CE          NaN   
29    2019-01-21   10800  2019-01-24    3          PE          NaN   
30    2019-01-22   11050  2019-01-24    2          CE          NaN   
31    2019-01-22   10850  2019-01-24    2          PE          NaN   
32    2019-01-23   11050  2019-01-24    1          CE          NaN   
33    2019-01-23   10800  2019-01-24    1          PE          NaN   
34    2019-01-24   10950  2019-01-24    0          CE          NaN   
35    2019-01-24   10750  2019-01-24    0          PE          NaN   
36    2019-01-25   10950  2019-01-31    6          CE        66.45   
37    2019-01-25   10750  2019-01-31    6          PE        25.30   
38    2019-01-28   10900  2019-01-31    3          CE        32.40   
39    2019-01-28   10700  2019-01-31    3          PE        50.00   
40    2019-01-29   10750  2019-01-31    2          CE        31.30   
41    2019-01-29   10550  2019-01-31    2          PE        38.20   
42    2019-01-30   10800  2019-01-31    1          CE        16.65   
43    2019-01-30   10600  2019-01-31    1          PE        16.05   
44    2019-01-31   10800  2019-01-31    0          CE         2.60   
45    2019-01-31   10600  2019-01-31    0          PE         3.80   
46    2019-02-01   10950  2019-02-07    6          CE          NaN   
47    2019-02-01   10750  2019-02-07    6          PE          NaN   
48    2019-02-04   11000  2019-02-07    3          CE          NaN   
49    2019-02-04   10750  2019-02-07    3          PE          NaN   
50    2019-02-05   11000  2019-02-07    2          CE          NaN   
51    2019-02-05   10800  2019-02-07    2          PE          NaN   
52    2019-02-06   11050  2019-02-07    1          CE          NaN   
53    2019-02-06   10850  2019-02-07    1          PE          NaN   
54    2019-02-07   11200  2019-02-07    0          CE          NaN   
55    2019-02-07   10950  2019-02-07    0          PE          NaN   
56    2019-02-08   1115

In [60]:
# tb = tb.drop(columns=['RSI on Entry', 'day'])

In [77]:
# tb.to_csv('Lobster_1_30_w_hedges.csv', index=False)

In [84]:
import pandas as pd

def calculate_dte_stats(df):
    """
    Calculate stats grouped by DTE: 
    - Returns Sum for each DTE
    - Max Drawdown (DD) for each DTE
    - Ratio of Returns Sum to Max DD for each DTE

    Parameters:
        df (pd.DataFrame): DataFrame containing a 'DTE' column, 'returns', and 'drawdown' columns.
    
    Returns:
        pd.DataFrame: DataFrame with aggregated statistics by DTE.
    """
    # print(df.columns)
    if 'DTE' not in df.columns or 'Total ROI%' not in df.columns or 'DD' not in df.columns:
        raise ValueError("DataFrame must contain 'DTE', 'returns', and 'drawdown' columns.")
    
    # Group by DTE and calculate required stats
    grouped_stats = df.groupby('DTE').agg(
        returns_sum=('Total ROI%', 'sum'),
        max_drawdown=('DD', 'min'),  # Assuming 'drawdown' contains negative values
        total_trades=('DTE', 'count')
    ).reset_index()
    
    # Calculate ratio of returns sum to max drawdown
    grouped_stats['returns_to_max_dd_ratio'] = (
        grouped_stats['returns_sum'] / grouped_stats['max_drawdown'].abs()
    )

    return grouped_stats


In [87]:
stats_dte = calculate_dte_stats(tb)
stats_dte[1:]

DTE  returns_sum  max_drawdown  total_trades  returns_to_max_dd_ratio
1    0   216.077355    -12.095041           622                17.864955
2    1   158.556458    -12.541781           590                12.642260
3    2   111.501167    -13.086746           594                 8.520160
4    3   101.348922    -14.555113           566                 6.963115
5    4     0.000000           NaN             4                      NaN
6    5     3.834230    -12.491741            32                 0.306941
7    6   129.145841    -13.698995           566                 9.427395